In [1]:
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.mpl.gridliner import LONGITUDE_FORMATTER, LATITUDE_FORMATTER
import matplotlib.pyplot as plt
import xarray as xr

import numpy as np
import metpy
import metpy.calc as mpcalc
from metpy.plots import ctables
from metpy.cbook import get_test_data
from metpy.units import units
import os
import scipy.integrate as integrate
import datetime as dt
import glob
import json
from datetime import datetime
from datetime import timedelta

from matplotlib.colors import Normalize
from matplotlib.colors import ListedColormap, LinearSegmentedColormap, BoundaryNorm

#import wrf
import scipy
#import xcape

In [2]:
os.chdir('/data/ecmwf')
#data = xr.open_dataset('ec_pl3_small.nc')
data_ml = xr.open_dataset('ec_ml.nc')
data_sfc = xr.open_dataset('ec_sfc2.nc')
#data_sfc2 = xr.open_dataset('ec_sfc.nc')

# View a summary of the Dataset
print(data_ml)
print(data_sfc)

<xarray.Dataset>
Dimensions:    (time: 48, longitude: 151, latitude: 101, level: 48)
Coordinates:
  * time       (time) datetime64[ns] 2023-02-03T01:00:00 ... 2023-02-05
  * longitude  (longitude) float32 0.0 0.1 0.2 0.3 0.4 ... 14.7 14.8 14.9 15.0
  * latitude   (latitude) float32 55.0 54.9 54.8 54.7 ... 45.3 45.2 45.1 45.0
  * level      (level) float64 90.0 91.0 92.0 93.0 ... 134.0 135.0 136.0 137.0
Data variables:
    u          (time, level, latitude, longitude) float32 ...
    v          (time, level, latitude, longitude) float32 ...
    q          (time, level, latitude, longitude) float32 ...
Attributes:
    CDI:          Climate Data Interface version ?? (http://mpimet.mpg.de/cdi)
    Conventions:  CF-1.6
    history:      Fri Feb 03 06:55:06 2023: cdo merge uwind_ml.nc vwind_ml.nc...
    CDO:          Climate Data Operators version 1.9.3 (http://mpimet.mpg.de/...
<xarray.Dataset>
Dimensions:    (longitude: 151, latitude: 101, time: 48)
Coordinates:
  * longitude  (longitude) 

In [3]:
# To parse the full dataset, we can call parse_cf without an argument, and assign the returned Dataset.

#data = data.metpy.parse_cf()
data_ml = data_ml.metpy.parse_cf()
data_sfc = data_sfc.metpy.parse_cf()

x, y = data_ml['u'].metpy.coordinates('x', 'y')

time = data_ml['u'].metpy.time

timeinit = time[0]
timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
print(timeinit)

sfcuwind =  data_sfc['u10']
sfcvwind =  data_sfc['v10']
mslp = data_sfc['msl']
mslp = mslp/100

#qv_bl = data_ml['q'].where(data_ml['q'].level>123, drop=True)
#qv_mean = np.mean(qv_bl, axis=1)
#qv_mean = qv_mean*1000

usfc = data_sfc['u10']
vsfc = data_sfc['v10']
t2 = data_sfc['t2m']
d2 = data_sfc['d2m']
z = data_sfc['z']
cape = data_sfc['mucape']
mlcape = data_sfc['mlcape50']
mlcin = data_sfc['mlcin50']
cin = data_sfc['cin']
li = data_sfc['litota1']
tcwv = data_sfc['tcwv']
u250m = data_ml['u'].metpy.loc[{'level': 129}]
v250m = data_ml['v'].metpy.loc[{'level': 129}]
u500m = data_ml['u'].metpy.loc[{'level': 124}]
v500m = data_ml['v'].metpy.loc[{'level': 124}]
u750m = data_ml['u'].metpy.loc[{'level': 121}]
v750m = data_ml['v'].metpy.loc[{'level': 121}]
u1km = data_ml['u'].metpy.loc[{'level': 117}]
v1km = data_ml['v'].metpy.loc[{'level': 117}]
u1_5km = data_ml['u'].metpy.loc[{'level': 114}]
v1_5km = data_ml['v'].metpy.loc[{'level': 114}]
u2km = data_ml['u'].metpy.loc[{'level': 110}]
v2km = data_ml['v'].metpy.loc[{'level': 110}]
u2_5km = data_ml['u'].metpy.loc[{'level': 108}]
v2_5km = data_ml['v'].metpy.loc[{'level': 108}]
u3km = data_ml['u'].metpy.loc[{'level': 105}]
v3km = data_ml['v'].metpy.loc[{'level': 105}]
u3_5km = data_ml['u'].metpy.loc[{'level': 103}]
v3_5km = data_ml['v'].metpy.loc[{'level': 103}]
u4km = data_ml['u'].metpy.loc[{'level': 101}]
v4km = data_ml['v'].metpy.loc[{'level': 101}]
u6km = data_ml['u'].metpy.loc[{'level': 94}]
v6km = data_ml['v'].metpy.loc[{'level': 94}]

q_ll = data_ml['q'].where(data_ml['q'].level>124, drop=True)
qmean = np.mean(q_ll, axis=1)

ulls = u1km - usfc
vlls = v1km - vsfc
umls = u3km - usfc
vmls = v3km - vsfc
udls = u6km - usfc
vdls = v6km - vsfc
lls = np.sqrt(ulls**2 + vlls**2)
mls = np.sqrt(umls**2 + vmls**2)
dls = np.sqrt(udls**2 + vdls**2)


u_motion = data_ml['u'].where(data_ml['u'].level>94, drop=True)
v_motion = data_ml['v'].where(data_ml['v'].level>94, drop=True)
umean = np.mean(u_motion, axis=1)
vmean = np.mean(v_motion, axis=1)
smotion = np.sqrt(umean**2 + vmean**2)
ubunkers = umean+(7.5/dls)*vdls
vbunkers = vmean-(7.5/dls)*udls

sr1=np.sqrt((usfc-ubunkers)**2+(vsfc-vbunkers)**2)
sr2=np.sqrt((u500m-ubunkers)**2+(v500m-vbunkers)**2)
sr3=np.sqrt((u1km-ubunkers)**2+(v1km-vbunkers)**2)
sr4=np.sqrt((u1_5km-ubunkers)**2+(v1_5km-vbunkers)**2)
sr5=np.sqrt((u2km-ubunkers)**2+(v2km-vbunkers)**2)
srmean_ll = (sr1+sr2+sr3+sr4+sr5)/5

sr6=np.sqrt((u2km-ubunkers)**2+(v2km-vbunkers)**2)
sr7=np.sqrt((u2_5km-ubunkers)**2+(v2_5km-vbunkers)**2)
sr8=np.sqrt((u3km-ubunkers)**2+(v3km-vbunkers)**2)
sr9=np.sqrt((u3_5km-ubunkers)**2+(v3_5km-vbunkers)**2)
sr10=np.sqrt((u4km-ubunkers)**2+(v4km-vbunkers)**2)
srmean_ul = (sr6+sr7+sr8+sr9+sr10)/5

sr1m=np.sqrt((usfc-umean)**2+(vsfc-vmean)**2)
sr2m=np.sqrt((u500m-umean)**2+(v500m-vmean)**2)
sr3m=np.sqrt((u1km-umean)**2+(v1km-vmean)**2)
sr4m=np.sqrt((u1_5km-umean)**2+(v1_5km-vmean)**2)
sr5m=np.sqrt((u2km-umean)**2+(v2km-vmean)**2)
srmean_llm = (sr1m+sr2m+sr3m+sr4m+sr5m)/5

sr6m=np.sqrt((u2km-umean)**2+(v2km-vmean)**2)
sr7m=np.sqrt((u2_5km-umean)**2+(v2_5km-vmean)**2)
sr8m=np.sqrt((u3km-umean)**2+(v3km-vmean)**2)
sr9m=np.sqrt((u3_5km-umean)**2+(v3_5km-vmean)**2)
sr10m=np.sqrt((u4km-umean)**2+(v4km-vmean)**2)
srmean_ulm = (sr6m+sr7m+sr8m+sr9m+sr10m)/5

srh2=((u500m-ubunkers)*(vsfc-vbunkers)-(usfc-ubunkers)*(v500m-vbunkers))
srh3=((u1km-ubunkers)*(v500m-vbunkers)-(u500m-ubunkers)*(v1km-vbunkers))
srh4=((u1_5km-ubunkers)*(v1km-vbunkers)-(u1km-ubunkers)*(v1_5km-vbunkers))
srh5=((u2km-ubunkers)*(v1_5km-vbunkers)-(u1_5km-ubunkers)*(v2km-vbunkers))
srh6=((u2_5km-ubunkers)*(v2km-vbunkers)-(u2km-ubunkers)*(v2_5km-vbunkers))
srh7=((u3km-ubunkers)*(v2_5km-vbunkers)-(u2_5km-ubunkers)*(v3km-vbunkers))

srh1a=((u250m-ubunkers)*(vsfc-vbunkers)-(usfc-ubunkers)*(v250m-vbunkers))
srh1b=((u500m-ubunkers)*(v250m-vbunkers)-(u250m-ubunkers)*(v500m-vbunkers))

#srh8=((u250m-ubunkers)*(vsfc-vbunkers)-(usfc-ubunkers)*(v250m-vbunkers))
#srh9=((u500m-ubunkers)*(v250m-vbunkers)-(u250m-ubunkers)*(v500m-vbunkers))
#srh10=((u750m-ubunkers)*(v500m-vbunkers)-(u500m-ubunkers)*(v750m-vbunkers))
#srh11=((u1km-ubunkers)*(v750m-vbunkers)-(u750m-ubunkers)*(v1km-vbunkers))

srh3km=srh2+srh3+srh4+srh5+srh6+srh7
srh1km=srh2+srh3
srh500m=srh1a+srh1b

wmaxshear = dls*np.sqrt(2*cape)

ehi3 = (cape*srh3km)/160000
ehi1 = (cape*srh1km)/160000

scp = mpcalc.supercell_composite(cape, srh3km*units('m/s*m/s'), dls*units('m/s'))
#scp = scp.where(scp<0.1,-0.01)
rh2 = mpcalc.relative_humidity_from_dewpoint(t2, d2)
lcl = (20+((t2-273.15)/5))*100*(1-rh2)  # after Lawrence 2005
stp = mpcalc.significant_tornado(cape, lcl*units('m'), srh1km*units('m/s*m/s'), dls*units('m/s'))
#stp = stp.where(scp<0.1,-0.01)

dx, dy = metpy.xarray.grid_deltas_from_dataarray(u500m)
div500 = mpcalc.divergence(u500m, v500m)
conv500 = np.ma.masked_where(div500>0,div500)
cin_new = data_sfc['cin'].where(data_sfc['cin']<0.01,-0.01)
mlcin_new = data_sfc['mlcin50'].where(data_sfc['mlcin50']<0.01,-0.01)
#print(conv500)
#np.max(cin)
#print(np.min(stp))

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00


In [4]:
def plot_background(ax):
    ax.set_extent([2, 9, 48, 51.5])
    ax.add_feature(cfeature.COASTLINE.with_scale('10m'), LineWidth=2)
    ax.add_feature(cfeature.BORDERS.with_scale('10m'),LineWidth=2)
    gl = ax.gridlines(draw_labels=True,linewidth=0.5, color='gray', alpha=0.5, linestyle='--')
    gl.top_labels = False
    gl.right_labels = False
    gl.xlabel_style = {'size': 12, 'color': 'black'}
    gl.ylabel_style = {'size': 12, 'color': 'black'}
    gl.xformatter = LONGITUDE_FORMATTER
    gl.yformatter = LATITUDE_FORMATTER
    return ax

#import matplotlib
#cmap = matplotlib.cm.get_cmap('cubehelix_r')
#for i in range(20):
    #rgba = cmap(i)
    # rgb2hex accepts rgb or rgba
    #print(rgba)

In [5]:
# Create the figure and plot background on different axes
for i in range(48):
    crs = ccrs.Mercator()
    fig, axarr = plt.subplots(nrows=2, ncols=2, figsize=(20, 15), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)

    clevs_cape = np.arange(100,5100,400)
    clevs_srh3 = np.arange(50,650,50)
    clevs_lls = np.arange(4,32,2)
    clevs_cin = [-25,0,25,50,75,100,125,150,175,200,225,250]
    clevs_conv = np.arange(-100,-10,20)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    cmap = plt.get_cmap('gist_ncar')
    newcmap1 = ListedColormap(cmap(np.linspace(0.15, 0.8, 31)))
    colors=[(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
    colors2 = [(1,1,1),
          (0.953,0.882,0.882),
          (0.933,0.784,0.792),
          (0.906,0.686,0.694),
          (0.871,0.584,0.592),
          (0.831,0.478,0.494),
          (0.784,0.369,0.388),
          (0.729,0.251,0.278),
          (0.643,0.141,0.184),
          (0.525,0.075,0.122),
          (0.412,0.000,0.047)]
           

    cmap1 = ListedColormap(colors)
    cmap2 = ListedColormap(colors2)
    newcmap = ListedColormap(cmap1(np.linspace(0, 1, 19)))

    time = data_sfc['mucape'].metpy.time
    data_crs = data_sfc['cin'].metpy.cartopy_crs
    # Upper left plot
    cf1 = axlist[0].contourf(data_ml.longitude, data_ml.latitude, cape.metpy.loc[{'time': time[i]}], 
                     clevs_cape, cmap=newcmap, extend='max', transform=data_crs)
    wind_slice = (slice(None, None, 4), slice(None, None, 4))
    c1=axlist[0].barbs(x[wind_slice[0]], y[wind_slice[1]],
            udls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            vdls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  pivot='middle', color='red',transform=data_crs, length=7,
                                     zorder=5)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[0].set_title('MU CAPE & 0-6 km Shear Vector', fontsize=16)
    cb1= fig.colorbar(cf1, ax=axlist[0], orientation='vertical',
                           ticks=(100,500,900,1300,1700,2100,2500,2900,3300,3700,4100,4500),
                              shrink=1, fraction=0.05, pad=0)
    cb1.set_label('J/kg', size='x-large')


    # Upper left plot
    cf2 = axlist[1].contourf(data_ml.longitude, data_ml.latitude, lls.metpy.loc[{'time': time[i]}], 
                     clevs_lls, cmap='BuPu', extend='max', transform=data_crs)
    wind_slice = (slice(None, None, 4), slice(None, None, 4))
    c2=axlist[1].barbs(x[wind_slice[0]], y[wind_slice[1]],
            umls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            vmls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  pivot='middle', color='red',transform=data_crs, length=7,
                                     zorder=5)
    ccf2 = axlist[1].contour(data_ml.longitude, data_ml.latitude, lls.metpy.loc[{'time': time[i]}], 
                     [10,15], colors='blue' , transform=data_crs)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[1].set_title('0-1 km Bulk Shear & 0-3 km Shear Vector', fontsize=16)
    cb2 = fig.colorbar(cf2, ax=axlist[1], orientation='vertical',
                           ticks=(4,6,8,10,12,14,16,18,20,22,24,26,28,30),shrink=1, fraction=0.05, pad=0)
    cb2.set_label('m/s', size='x-large')
    axlist[1].clabel(ccf2, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    
    # Upper left plot
    cf3 = axlist[2].contourf(data_ml.longitude, data_ml.latitude, cin_new.metpy.loc[{'time': time[i]}], 
                     clevs_cin, cmap=cmap2, extend='max', transform=data_crs)
    ccf3= axlist[2].contour(data_ml.longitude, data_ml.latitude, div500[i,:,:]*100000,
                     [-100,-50,-30,-10], colors='blue', linestyles='dashed', transform=data_crs)
    axlist[2].clabel(ccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[2].set_title('MU CIN & 500 m Convergence (≤ -10x10⁻⁵ s⁻¹)', fontsize=16)
    cb3 = fig.colorbar(cf3, ax=axlist[2], orientation='vertical',
                           ticks=(0,25,50,75,100,125,150,175,200,225), shrink=1, fraction=0.05, pad=0)
    cb3.set_label('J/kg', size='x-large')

    # Upper left plot
    cf4 = axlist[3].contourf(data_ml.longitude, data_ml.latitude, srh3km.metpy.loc[{'time': time[i]}], 
                     clevs_srh3, cmap='plasma_r', extend='max',transform=data_crs)
    ccf4 = axlist[3].contour(data_ml.longitude, data_ml.latitude, srh1km.metpy.loc[{'time': time[i]}], 
                     [100,150,200,300], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[3].clabel(ccf4, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[3].set_title('0-3 km SRH & 0-1 km SRH (dotted lines)', fontsize=16)
    cb4 = fig.colorbar(cf4, ax=axlist[3], orientation='vertical',
                           ticks=(50,100,150,200,250,300,350,400,450,500,550,600),shrink=1, fraction=0.05, pad=0)
    cb4.set_label('m²/s²', size='x-large')
    
    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)

    # Set figure title
    plt.gcf().text(0.13, 0.94, 'Model: ECMWF IFS 0.1° | '+timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+data_ml['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.4, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.5, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+data_sfc['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    plt.gcf().text(0.55, 0.09, 'Note: SRH is calculated for a right-moving storm cell.', fontsize=10)

    # Display the plot
    time2 = str(i+1)
    base_filename='ecmwf_comp_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=85)
    plt.close("all")

ecmwf_comp_1.jpeg


/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


ecmwf_comp_2.jpeg
ecmwf_comp_3.jpeg
ecmwf_comp_4.jpeg
ecmwf_comp_5.jpeg
ecmwf_comp_6.jpeg
ecmwf_comp_7.jpeg
ecmwf_comp_8.jpeg
ecmwf_comp_9.jpeg
ecmwf_comp_10.jpeg
ecmwf_comp_11.jpeg
ecmwf_comp_12.jpeg
ecmwf_comp_13.jpeg
ecmwf_comp_14.jpeg
ecmwf_comp_15.jpeg
ecmwf_comp_16.jpeg
ecmwf_comp_17.jpeg
ecmwf_comp_18.jpeg
ecmwf_comp_19.jpeg
ecmwf_comp_20.jpeg
ecmwf_comp_21.jpeg
ecmwf_comp_22.jpeg
ecmwf_comp_23.jpeg
ecmwf_comp_24.jpeg
ecmwf_comp_25.jpeg
ecmwf_comp_26.jpeg
ecmwf_comp_27.jpeg
ecmwf_comp_28.jpeg
ecmwf_comp_29.jpeg
ecmwf_comp_30.jpeg
ecmwf_comp_31.jpeg
ecmwf_comp_32.jpeg
ecmwf_comp_33.jpeg
ecmwf_comp_34.jpeg
ecmwf_comp_35.jpeg
ecmwf_comp_36.jpeg
ecmwf_comp_37.jpeg
ecmwf_comp_38.jpeg
ecmwf_comp_39.jpeg
ecmwf_comp_40.jpeg
ecmwf_comp_41.jpeg
ecmwf_comp_42.jpeg
ecmwf_comp_43.jpeg
ecmwf_comp_44.jpeg
ecmwf_comp_45.jpeg
ecmwf_comp_46.jpeg
ecmwf_comp_47.jpeg
ecmwf_comp_48.jpeg


In [ ]:
# Create the figure and plot background on different axes
for i in range(48):
    crs = ccrs.Mercator()
    fig, axarr = plt.subplots(nrows=2, ncols=2, figsize=(20, 15), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)

    clevs_cape = np.arange(100,5100,400)
    clevs_srh3 = np.arange(50,650,50)
    clevs_lls = np.arange(4,32,2)
    clevs_cin = [-25,0,25,50,75,100,125,150,175,200,225,250]
    clevs_conv = np.arange(-100,-10,20)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    cmap = plt.get_cmap('gist_ncar')
    newcmap1 = ListedColormap(cmap(np.linspace(0.15, 0.8, 31)))
    colors=[(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
    colors2 = [(1,1,1),
          (0.953,0.882,0.882),
          (0.933,0.784,0.792),
          (0.906,0.686,0.694),
          (0.871,0.584,0.592),
          (0.831,0.478,0.494),
          (0.784,0.369,0.388),
          (0.729,0.251,0.278),
          (0.643,0.141,0.184),
          (0.525,0.075,0.122),
          (0.412,0.000,0.047)]
           

    cmap1 = ListedColormap(colors)
    cmap2 = ListedColormap(colors2)
    newcmap = ListedColormap(cmap1(np.linspace(0, 1, 19)))

    time = data_sfc['mlcape50'].metpy.time
    data_crs = data_sfc['cin'].metpy.cartopy_crs
    # Upper left plot
    cf1 = axlist[0].contourf(data_ml.longitude, data_ml.latitude, mlcape.metpy.loc[{'time': time[i]}], 
                     clevs_cape, cmap=newcmap, extend='max', transform=data_crs)
    wind_slice = (slice(None, None, 4), slice(None, None, 4))
    c1=axlist[0].barbs(x[wind_slice[0]], y[wind_slice[1]],
            udls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            vdls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  pivot='middle', color='red',transform=data_crs, length=7,
                                     zorder=5)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[0].set_title('ML CAPE & 0-6 km Shear Vector', fontsize=16)
    cb1= fig.colorbar(cf1, ax=axlist[0], orientation='vertical',
                           ticks=(100,500,900,1300,1700,2100,2500,2900,3300,3700,4100,4500),
                              shrink=1, fraction=0.05, pad=0)
    cb1.set_label('J/kg', size='x-large')


    # Upper left plot
    cf2 = axlist[1].contourf(data_ml.longitude, data_ml.latitude, lls.metpy.loc[{'time': time[i]}], 
                     clevs_lls, cmap='BuPu', extend='max', transform=data_crs)
    wind_slice = (slice(None, None, 4), slice(None, None, 4))
    c2=axlist[1].barbs(x[wind_slice[0]], y[wind_slice[1]],
            umls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            vmls.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  pivot='middle', color='red',transform=data_crs, length=7,
                                     zorder=5)
    ccf2 = axlist[1].contour(data_ml.longitude, data_ml.latitude, lls.metpy.loc[{'time': time[i]}], 
                     [10,15], colors='blue' , transform=data_crs)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[1].set_title('0-1 km Bulk Shear & 0-3 km Shear Vector', fontsize=16)
    cb2 = fig.colorbar(cf2, ax=axlist[1], orientation='vertical',
                           ticks=(4,6,8,10,12,14,16,18,20,22,24,26,28,30),shrink=1, fraction=0.05, pad=0)
    cb2.set_label('m/s', size='x-large')
    axlist[1].clabel(ccf2, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    
    # Upper left plot
    cf3 = axlist[2].contourf(data_ml.longitude, data_ml.latitude, mlcin_new.metpy.loc[{'time': time[i]}], 
                     clevs_cin, cmap=cmap2, extend='max', transform=data_crs)
    ccf3= axlist[2].contour(data_ml.longitude, data_ml.latitude, div500[i,:,:]*100000,
                     [-100,-50,-30,-10], colors='blue', linestyles='dashed', transform=data_crs)
    axlist[2].clabel(ccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[2].set_title('ML CIN & 500 m Convergence (≤ -10x10⁻⁵ s⁻¹)', fontsize=16)
    cb3 = fig.colorbar(cf3, ax=axlist[2], orientation='vertical',
                           ticks=(0,25,50,75,100,125,150,175,200,225), shrink=1, fraction=0.05, pad=0)
    cb3.set_label('J/kg', size='x-large')

    # Upper left plot
    cf4 = axlist[3].contourf(data_ml.longitude, data_ml.latitude, srh3km.metpy.loc[{'time': time[i]}], 
                     clevs_srh3, cmap='plasma_r', extend='max',transform=data_crs)
    ccf4 = axlist[3].contour(data_ml.longitude, data_ml.latitude, srh1km.metpy.loc[{'time': time[i]}], 
                     [100,150,200,300], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[3].clabel(ccf4, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[3].set_title('0-3 km SRH & 0-1 km SRH (dotted lines)', fontsize=16)
    cb4 = fig.colorbar(cf4, ax=axlist[3], orientation='vertical',
                           ticks=(50,100,150,200,250,300,350,400,450,500,550,600),shrink=1, fraction=0.05, pad=0)
    cb4.set_label('m²/s²', size='x-large')
    
    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)

    # Set figure title
    plt.gcf().text(0.13, 0.94, 'Model: ECMWF IFS 0.1° | '+timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+data_ml['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.4, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.5, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+data_sfc['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    plt.gcf().text(0.55, 0.09, 'Note: SRH is calculated for a right-moving storm cell.', fontsize=10)

    # Display the plot
    time2 = str(i+1)
    base_filename='ecmwf_comp3_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=85)
    plt.close("all")

In [97]:
# Create the figure and plot background on different axes
for i in range(48):
    crs = ccrs.Mercator()
    fig, axarr = plt.subplots(nrows=1, ncols=2, figsize=(25, 10), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)

    clevs_wmax = np.arange(-100,2500,200)
    clevs_tcwv = np.arange(0,55,5)
    clevs_lls = np.arange(4,30,2)
    clevs_cin = [-25,0,25,50,75,100,125,150,175,200,225,250]
    clevs_qv = np.arange(0,20,2)
    clevs_mslp = np.arange(950, 1050, 1)
    #clevs_ehi = np.arange(-0.5, 6.5,0.5)
    cmap3 = plt.get_cmap('cubehelix_r')
    newcmap3 = ListedColormap(cmap3(np.linspace(0, 0.9, 20)))
    bounds = [0,0.1,0.2,0.5,1,2,3,4,5]
    norm = BoundaryNorm(bounds, newcmap3.N)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    cmap = plt.get_cmap('gist_ncar')
    newcmap1 = ListedColormap(cmap(np.linspace(0.15, 0.8, 30)))
    colors=[(1,1,1),(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
    colors2 = [(1,1,1),
          (0.953,0.882,0.882),
          (0.933,0.784,0.792),
          (0.906,0.686,0.694),
          (0.871,0.584,0.592),
          (0.831,0.478,0.494),
          (0.784,0.369,0.388),
          (0.729,0.251,0.278),
          (0.643,0.141,0.184),
          (0.525,0.075,0.122),
          (0.412,0.000,0.047)]
           

    cmap1 = ListedColormap(colors)
    cmap2 = ListedColormap(colors2)
    newcmap = ListedColormap(cmap1(np.linspace(0, 1, 17)))

    time = data_sfc['mucape'].metpy.time
    data_crs = data_sfc['cin'].metpy.cartopy_crs
    # Upper left plot

    
    # Upper left plot
    cf3 = axlist[0].contourf(data_ml.longitude, data_ml.latitude, qmean.metpy.loc[{'time': time[i]}]*1000, 
                     clevs_qv, cmap='YlGnBu', extend='max', transform=data_crs)
    ccf3= axlist[0].contour(data_ml.longitude, data_ml.latitude, mslp.metpy.loc[{'time': time[i]}],
                     clevs_mslp, colors='black', transform=data_crs)
    cccf3 = axlist[0].contour(data_ml.longitude, data_ml.latitude, qmean.metpy.loc[{'time': time[i]}]*1000, 
                     [6,10,14], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[0].clabel(ccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[0].clabel(cccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[0].set_title('MSLP & 0-500 m Mean Specific Humidity', fontsize=16)
    cb3 = fig.colorbar(cf3, ax=axlist[0], orientation='vertical', shrink=0.81, fraction=0.1, pad=0)
    cb3.set_label('g/kg', size='x-large')

    # Upper left plot
    cf4 = axlist[1].contourf(data_ml.longitude, data_ml.latitude, tcwv.metpy.loc[{'time': time[i]}], 
                     clevs_tcwv, cmap='BrBG', extend='max',transform=data_crs)
    ccf4 = axlist[1].contour(data_ml.longitude, data_ml.latitude, tcwv.metpy.loc[{'time': time[i]}], 
                     [10,20,30,40,50], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[1].clabel(ccf4, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[1].set_title('Precipitable Water & Storm Motion Vector', fontsize=16)
    wind_slice = (slice(None, None, 4), slice(None, None, 4))
    c4=axlist[1].barbs(x[wind_slice[0]], y[wind_slice[1]],
            umean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            vmean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  pivot='middle', color='red',transform=data_crs, length=7,
                                     zorder=3)
    cb4 = fig.colorbar(cf4, ax=axlist[1], ticks=(0,5,10,15,20,25,30,35,40,45,50), orientation='vertical',shrink=0.81, fraction=0.1, pad=0)
    cb4.set_label('mm', size='x-large')
    
    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)

    # Set figure title
    plt.gcf().text(0.125, 0.88, 'Model: ECMWF IFS 0.1° | '+timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+data_ml['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.4, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.5, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+data_sfc['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    plt.gcf().text(0.55, 0.13, 'Note: Motion of a non-deviant storm cell.', fontsize=10)

    # Display the plot
    time2 = str(i+1)
    base_filename='ecmwf_comp2_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=85)
    plt.close("all")

ecmwf_comp2_1.jpeg
ecmwf_comp2_2.jpeg
ecmwf_comp2_3.jpeg
ecmwf_comp2_4.jpeg
ecmwf_comp2_5.jpeg
ecmwf_comp2_6.jpeg
ecmwf_comp2_7.jpeg
ecmwf_comp2_8.jpeg
ecmwf_comp2_9.jpeg
ecmwf_comp2_10.jpeg
ecmwf_comp2_11.jpeg
ecmwf_comp2_12.jpeg
ecmwf_comp2_13.jpeg
ecmwf_comp2_14.jpeg
ecmwf_comp2_15.jpeg
ecmwf_comp2_16.jpeg
ecmwf_comp2_17.jpeg
ecmwf_comp2_18.jpeg
ecmwf_comp2_19.jpeg
ecmwf_comp2_20.jpeg
ecmwf_comp2_21.jpeg
ecmwf_comp2_22.jpeg
ecmwf_comp2_23.jpeg
ecmwf_comp2_24.jpeg
ecmwf_comp2_25.jpeg
ecmwf_comp2_26.jpeg
ecmwf_comp2_27.jpeg
ecmwf_comp2_28.jpeg
ecmwf_comp2_29.jpeg
ecmwf_comp2_30.jpeg
ecmwf_comp2_31.jpeg
ecmwf_comp2_32.jpeg
ecmwf_comp2_33.jpeg
ecmwf_comp2_34.jpeg
ecmwf_comp2_35.jpeg
ecmwf_comp2_36.jpeg
ecmwf_comp2_37.jpeg
ecmwf_comp2_38.jpeg
ecmwf_comp2_39.jpeg
ecmwf_comp2_40.jpeg
ecmwf_comp2_41.jpeg
ecmwf_comp2_42.jpeg
ecmwf_comp2_43.jpeg
ecmwf_comp2_44.jpeg
ecmwf_comp2_45.jpeg
ecmwf_comp2_46.jpeg
ecmwf_comp2_47.jpeg
ecmwf_comp2_48.jpeg


In [12]:
# Create the figure and plot background on different axes
for i in range(48):
    crs = ccrs.Mercator()
    fig, axarr = plt.subplots(nrows=2, ncols=2, figsize=(20, 15), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)

    clevs_wmax = np.arange(-100,2500,200)
    clevs_scp = np.arange(0,17,1)
    clevs_stp = np.arange(0,4,0.2)
    clevs_tcwv = np.arange(0,55,5)
    clevs_lls = np.arange(4,30,2)
    clevs_cin = [-25,0,25,50,75,100,125,150,175,200,225,250]
    clevs_qv = np.arange(0,20,2)
    clevs_mslp = np.arange(950, 1050, 1)
    #clevs_ehi = np.arange(-0.5, 6.5,0.5)
    cmap3 = plt.get_cmap('cubehelix_r')
    newcmap3 = ListedColormap(cmap3(np.linspace(0, 0.9, 20)))
    bounds = [0,0.1,0.3,0.5,1,2,3,4,5]
    norm = BoundaryNorm(bounds, newcmap3.N)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    cmap = plt.get_cmap('gist_ncar')
    newcmap1 = ListedColormap(cmap(np.linspace(0.15, 0.8, 30)))
    colors=[(1,1,1),(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
    colors2 = [(1,1,1),
          (0.953,0.882,0.882),
          (0.933,0.784,0.792),
          (0.906,0.686,0.694),
          (0.871,0.584,0.592),
          (0.831,0.478,0.494),
          (0.784,0.369,0.388),
          (0.729,0.251,0.278),
          (0.643,0.141,0.184),
          (0.525,0.075,0.122),
          (0.412,0.000,0.047)]
           

    cmap1 = ListedColormap(colors)
    cmap2 = ListedColormap(colors2)
    newcmap = ListedColormap(cmap1(np.linspace(0, 1, 17)))

    time = data_sfc['mucape'].metpy.time
    data_crs = data_sfc['cin'].metpy.cartopy_crs
    # Upper left plot
    cf1 = axlist[0].contourf(data_ml.longitude, data_ml.latitude, wmaxshear.metpy.loc[{'time': time[i]}], 
                     clevs_wmax, cmap=newcmap, extend='max',transform=data_crs)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[0].set_title('WMAXSHEAR', fontsize=16)
    cb1= fig.colorbar(cf1, ax=axlist[0], orientation='vertical',
                           ticks=(100,300,500,700,900,1100,1300,1500,1700,1900,2100),
                              shrink=1, fraction=0.05, pad=0)
    cb1.set_label('m²/s²', size='x-large')
    plt.gcf().text(0.13, 0.50, 'Note: WMAXSHEAR is calculated as follows: sqrt(2 x MU CAPE) x (0-6 km bulk shear)', fontsize=10)


    # Upper left plot
    cf2 = axlist[1].contourf(data_ml.longitude, data_ml.latitude, ehi3.metpy.loc[{'time': time[i]}], 
                      [0,0.1,0.3,0.5,1,2,3,4,5], cmap=newcmap3, norm=norm, transform=data_crs)
    #ccf2 = axlist[1].contour(data_ml.longitude, data_ml.latitude, ehi1.metpy.loc[{'time': time[i]}], 
                     #[0.1,1], colors='blue' , transform=data_crs)
    #axlist[0].clabel(c1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[1].set_title('0-3 km EHI', fontsize=16)
    cb2 = fig.colorbar(cf2, ax=axlist[1], orientation='vertical', shrink=1, fraction=0.05, pad=0)
    #cb2.set_label('', size='x-large')
    #cb2.set_ticks([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10])
    #axlist[1].clabel(ccf2, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    plt.gcf().text(0.55, 0.50, 'Note: EHI is calculated as follows: (MU CAPE x SRH)/(1.6 x 10⁵)', fontsize=10)
    
    # Upper left plot
    cf3 = axlist[2].contourf(data_ml.longitude, data_ml.latitude, scp.metpy.loc[{'time': time[i]}], 
                      clevs_scp, cmap='PuRd', extend='max', transform=data_crs)
    ccf3= axlist[2].contour(data_ml.longitude, data_ml.latitude, scp.metpy.loc[{'time': time[i]}],
                     [1,4,10], colors='black', linestyles='dotted', transform=data_crs)
    #cccf3 = axlist[2].contour(data_ml.longitude, data_ml.latitude, qmean.metpy.loc[{'time': time[i]}]*1000, 
                     #[6,10,14], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[2].clabel(ccf3, fontsize=10, fmt='%i', rightside_up=True)
    #axlist[2].clabel(cccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[2].set_title('Supercell Composite Parameter', fontsize=16)
    cb3 = fig.colorbar(cf3, ax=axlist[2], orientation='vertical', 
                       ticks=(0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16), shrink=1, fraction=0.05, pad=0)
    cb3.set_label('', size='x-large')

    # Upper left plot
    cf4 = axlist[3].contourf(data_ml.longitude, data_ml.latitude, stp.metpy.loc[{'time': time[i]}], 
                     clevs_stp, cmap='Reds', extend='max',transform=data_crs)
    ccf4 = axlist[3].contour(data_ml.longitude, data_ml.latitude, stp.metpy.loc[{'time': time[i]}], 
                     [0.6,1.2,3], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[3].clabel(ccf4, fontsize=10, inline=1, inline_spacing=1, fmt='%1.1f', rightside_up=True)
    axlist[3].set_title('Significant Tornado Parameter', fontsize=16)
    #wind_slice = (slice(None, None, 4), slice(None, None, 4))
    #c4=axlist[3].barbs(x[wind_slice[0]], y[wind_slice[1]],
            #umean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            #vmean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  #pivot='middle', color='red',transform=data_crs, length=7,
                                     #zorder=3)
    cb4 = fig.colorbar(cf4, ax=axlist[3],   
                       orientation='vertical',shrink=1, fraction=0.05, pad=0)
    cb4.set_label('', size='x-large')
    
    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)

    # Set figure title
    plt.gcf().text(0.13, 0.94, 'Model: ECMWF IFS 0.1° | '+timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+data_ml['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.4, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.5, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+data_sfc['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.55, 0.09, 'Note: STP is calculated as follows: (MU CAPE x SRH)/(1.6 x 10⁵)', fontsize=10)

    # Display the plot
    time2 = str(i+1)
    base_filename='ecmwf_comp4_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=85)
    plt.close("all")

/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/geoaxes.py:1548: UserWarning: No contour levels were found within the data range.
  result = matplotlib.axes.Axes.contour(self, *args, **kwargs)
/home/lmathias/anaconda3/envs/metpy/lib/python3.9/site-packages/cartopy/mpl/feature_artist.py:211: MatplotlibDeprecationWarning: Case-insensitive properties were deprecated in 3.3 and support will be removed two minor releases later
  c = matplotlib.collections.PathCollection(paths,


ecmwf_comp4_1.jpeg
ecmwf_comp4_2.jpeg
ecmwf_comp4_3.jpeg
ecmwf_comp4_4.jpeg
ecmwf_comp4_5.jpeg
ecmwf_comp4_6.jpeg
ecmwf_comp4_7.jpeg
ecmwf_comp4_8.jpeg
ecmwf_comp4_9.jpeg
ecmwf_comp4_10.jpeg
ecmwf_comp4_11.jpeg
ecmwf_comp4_12.jpeg
ecmwf_comp4_13.jpeg
ecmwf_comp4_14.jpeg
ecmwf_comp4_15.jpeg
ecmwf_comp4_16.jpeg
ecmwf_comp4_17.jpeg
ecmwf_comp4_18.jpeg
ecmwf_comp4_19.jpeg
ecmwf_comp4_20.jpeg
ecmwf_comp4_21.jpeg
ecmwf_comp4_22.jpeg
ecmwf_comp4_23.jpeg
ecmwf_comp4_24.jpeg
ecmwf_comp4_25.jpeg
ecmwf_comp4_26.jpeg
ecmwf_comp4_27.jpeg
ecmwf_comp4_28.jpeg
ecmwf_comp4_29.jpeg
ecmwf_comp4_30.jpeg
ecmwf_comp4_31.jpeg
ecmwf_comp4_32.jpeg
ecmwf_comp4_33.jpeg
ecmwf_comp4_34.jpeg
ecmwf_comp4_35.jpeg
ecmwf_comp4_36.jpeg
ecmwf_comp4_37.jpeg
ecmwf_comp4_38.jpeg
ecmwf_comp4_39.jpeg
ecmwf_comp4_40.jpeg
ecmwf_comp4_41.jpeg
ecmwf_comp4_42.jpeg
ecmwf_comp4_43.jpeg
ecmwf_comp4_44.jpeg
ecmwf_comp4_45.jpeg
ecmwf_comp4_46.jpeg
ecmwf_comp4_47.jpeg
ecmwf_comp4_48.jpeg


In [8]:
# Create the figure and plot background on different axes
for i in range(48):
    crs = ccrs.Mercator()
    fig, axarr = plt.subplots(nrows=2, ncols=2, figsize=(20, 15), constrained_layout=False,
                              subplot_kw={'projection': crs})

    axlist = axarr.flatten()
    for ax in axlist:
        plot_background(ax)

    clevs_wmax = np.arange(-100,2500,200)
    clevs_scp = np.arange(0,17,1)
    clevs_stp = np.arange(0,4,0.2)
    clevs_tcwv = np.arange(0,55,5)
    clevs_lls = np.arange(0,24,2)
    clevs_cin = [-25,0,25,50,75,100,125,150,175,200,225,250]
    clevs_qv = np.arange(0,20,2)
    clevs_mslp = np.arange(950, 1050, 1)
    #clevs_ehi = np.arange(-0.5, 6.5,0.5)
    cmap3 = plt.get_cmap('cubehelix_r')
    newcmap3 = ListedColormap(cmap3(np.linspace(0, 0.9, 20)))
    bounds = [0,0.1,0.3,0.5,1,2,3,4,5]
    norm = BoundaryNorm(bounds, newcmap3.N)
    # cmap = plt.get_cmap('gist_ncar')
    # newcmap = ListedColormap(cmap(np.linspace(0.15, 0.9, 30)))
    cmap = plt.get_cmap('gist_ncar')
    newcmap1 = ListedColormap(cmap(np.linspace(0.15, 0.8, 30)))
    colors=[(1,1,1),(0.0, 0.9254901960784314, 0.9254901960784314), 
                        (0.00392156862745098, 0.6274509803921569, 0.9647058823529412), 
                        (0.0, 0.0, 0.9647058823529412), 
                        (0.0, 1.0, 0.0), 
                        (0.0, 0.7843137254901961, 0.0), 
                        (0.0, 0.5647058823529412, 0.0), 
                        (1.0, 1.0, 0.0), 
                        (0.9058823529411765, 0.7529411764705882, 0.0), 
                        (1.0, 0.5647058823529412, 0.0), 
                        (1.0, 0.16078431372, 0.16078431372), 
                        (0.7529411764705882, 0.0, 0.0),
                        (0.59765625, 0.0, 0.0), 
                        (1.0, 0.0, 1.0), 
                        (0.6, 0.3333333333333333, 0.788235294117647),
                         (0.27,0,0.4)]
    colors2 = [(1,1,1),
          (0.953,0.882,0.882),
          (0.933,0.784,0.792),
          (0.906,0.686,0.694),
          (0.871,0.584,0.592),
          (0.831,0.478,0.494),
          (0.784,0.369,0.388),
          (0.729,0.251,0.278),
          (0.643,0.141,0.184),
          (0.525,0.075,0.122),
          (0.412,0.000,0.047)]
           

    cmap1 = ListedColormap(colors)
    cmap2 = ListedColormap(colors2)
    newcmap = ListedColormap(cmap1(np.linspace(0, 1, 17)))

    time = data_sfc['mucape'].metpy.time
    data_crs = data_sfc['cin'].metpy.cartopy_crs
    # Upper left plot
    cf1 = axlist[0].contourf(data_ml.longitude, data_ml.latitude, srmean_ll.metpy.loc[{'time': time[i]}], 
                     clevs_lls, cmap='BuPu', extend='max',transform=data_crs)
    ccf1 = axlist[0].contour(data_ml.longitude, data_ml.latitude, srmean_ll.metpy.loc[{'time': time[i]}], 
                     [5,10,15,20], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[0].clabel(ccf1, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[0].set_title('0-2 km Mean Storm-Relative Wind (RM)', fontsize=16)
    cb1= fig.colorbar(cf1, ax=axlist[0], orientation='vertical',
                                                         shrink=1, fraction=0.05, pad=0)
    cb1.set_label('m/s', size='x-large')
    #plt.gcf().text(0.13, 0.50, 'Note: WMAXSHEAR is calculated as follows: sqrt(2 x MU CAPE) x (0-6 km bulk shear)', fontsize=10)


    # Upper left plot
    cf2 = axlist[1].contourf(data_ml.longitude, data_ml.latitude, srmean_llm.metpy.loc[{'time': time[i]}], 
                      clevs_lls, cmap='BuPu', extend='max', transform=data_crs)
    ccf2 = axlist[1].contour(data_ml.longitude, data_ml.latitude, srmean_llm.metpy.loc[{'time': time[i]}], 
                     [5,10,15,20], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[1].clabel(ccf2, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[1].set_title('0-2 km Mean Storm-Relative Wind (non-deviant motion)', fontsize=16)
    cb2 = fig.colorbar(cf2, ax=axlist[1], orientation='vertical', shrink=1, fraction=0.05, pad=0)
    cb2.set_label('m/s', size='x-large')
    #cb2.set_ticks([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10])
    #axlist[1].clabel(ccf2, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    #plt.gcf().text(0.55, 0.50, 'Note: EHI is calculated as follows: (MU CAPE x SRH)/(1.6 x 10⁵)', fontsize=10)
    
    # Upper left plot
    cf3 = axlist[2].contourf(data_ml.longitude, data_ml.latitude, srmean_ul.metpy.loc[{'time': time[i]}], 
                      clevs_lls, cmap='BuPu', extend='max', transform=data_crs)
    ccf3= axlist[2].contour(data_ml.longitude, data_ml.latitude, srmean_ul.metpy.loc[{'time': time[i]}],
                     [5,10,15,20], colors='black', linestyles='dotted', transform=data_crs)
    #cccf3 = axlist[2].contour(data_ml.longitude, data_ml.latitude, qmean.metpy.loc[{'time': time[i]}]*1000, 
                     #[6,10,14], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[2].clabel(ccf3, fontsize=10, fmt='%i', rightside_up=True)
    #axlist[2].clabel(cccf3, fontsize=10, fmt='%i', rightside_up=True)
    axlist[2].set_title('2-4 km Mean Storm-Relative Wind (RM)', fontsize=16)
    cb3 = fig.colorbar(cf3, ax=axlist[2], orientation='vertical', 
                        shrink=1, fraction=0.05, pad=0)
    cb3.set_label('m/s', size='x-large')

    # Upper left plot
    cf4 = axlist[3].contourf(data_ml.longitude, data_ml.latitude, srmean_ulm.metpy.loc[{'time': time[i]}], 
                     clevs_lls, cmap='BuPu', extend='max',transform=data_crs)
    ccf4 = axlist[3].contour(data_ml.longitude, data_ml.latitude, srmean_ulm.metpy.loc[{'time': time[i]}], 
                     [5,10,15,20], colors='black' , linestyles='dotted', transform=data_crs)
    axlist[3].clabel(ccf4, fontsize=10, inline=1, inline_spacing=1, fmt='%i', rightside_up=True)
    axlist[3].set_title('2-4 km Mean Storm-Relative Wind (non-deviant motion)', fontsize=16)
    #wind_slice = (slice(None, None, 4), slice(None, None, 4))
    #c4=axlist[3].barbs(x[wind_slice[0]], y[wind_slice[1]],
            #umean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
            #vmean.metpy.loc[{'time': time[i]}].values[wind_slice[0], wind_slice[1]]*1.94384,
                                  #pivot='middle', color='red',transform=data_crs, length=7,
                                     #zorder=3)
    cb4 = fig.colorbar(cf4, ax=axlist[3],   
                       orientation='vertical',shrink=1, fraction=0.05, pad=0)
    cb4.set_label('m/s', size='x-large')
    
    # Set height padding for plots
    fig.set_constrained_layout_pads(w_pad=0., h_pad=10, hspace=0., wspace=0.)

    # Set figure title
    plt.gcf().text(0.13, 0.94, 'Model: ECMWF IFS 0.1° | '+timeinit.strftime('Init: %d.%m.%Y %H:%M UTC | ')+data_ml['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.4, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC'), fontsize=20)
    #plt.gcf().text(0.5, 0.94, timeinit.strftime('Init: %d.%m.%Y %H:%M UTC / ')+data_sfc['time'][i].dt.strftime('Valid: %d.%m.%Y %H:%M UTC').values, fontsize=20)
    #plt.gcf().text(0.55, 0.09, 'Note: STP is calculated as follows: (MU CAPE x SRH)/(1.6 x 10⁵)', fontsize=10)

    # Display the plot
    time2 = str(i+1)
    base_filename='ecmwf_srwind_'
    suffix='.jpeg'
    latest='latest'
    my_file = base_filename+time2+suffix
    print(my_file)
    plt.savefig(my_file, format="jpeg", bbox_inches='tight', dpi=85)
    plt.close("all")

ecmwf_srwind_1.jpeg
ecmwf_srwind_2.jpeg
ecmwf_srwind_3.jpeg
ecmwf_srwind_4.jpeg
ecmwf_srwind_5.jpeg
ecmwf_srwind_6.jpeg
ecmwf_srwind_7.jpeg
ecmwf_srwind_8.jpeg
ecmwf_srwind_9.jpeg
ecmwf_srwind_10.jpeg
ecmwf_srwind_11.jpeg
ecmwf_srwind_12.jpeg
ecmwf_srwind_13.jpeg
ecmwf_srwind_14.jpeg
ecmwf_srwind_15.jpeg
ecmwf_srwind_16.jpeg
ecmwf_srwind_17.jpeg
ecmwf_srwind_18.jpeg
ecmwf_srwind_19.jpeg
ecmwf_srwind_20.jpeg
ecmwf_srwind_21.jpeg
ecmwf_srwind_22.jpeg
ecmwf_srwind_23.jpeg
ecmwf_srwind_24.jpeg
ecmwf_srwind_25.jpeg
ecmwf_srwind_26.jpeg
ecmwf_srwind_27.jpeg
ecmwf_srwind_28.jpeg
ecmwf_srwind_29.jpeg
ecmwf_srwind_30.jpeg
ecmwf_srwind_31.jpeg
ecmwf_srwind_32.jpeg
ecmwf_srwind_33.jpeg
ecmwf_srwind_34.jpeg
ecmwf_srwind_35.jpeg
ecmwf_srwind_36.jpeg
ecmwf_srwind_37.jpeg
ecmwf_srwind_38.jpeg
ecmwf_srwind_39.jpeg
ecmwf_srwind_40.jpeg
ecmwf_srwind_41.jpeg
ecmwf_srwind_42.jpeg
ecmwf_srwind_43.jpeg
ecmwf_srwind_44.jpeg
ecmwf_srwind_45.jpeg
ecmwf_srwind_46.jpeg
ecmwf_srwind_47.jpeg
ecmwf_srwind_48.jpeg
